In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
%matplotlib inline
import matplotlib.pyplot as plt

In [3]:
import pandas as pd
import numpy as np
import os

In [4]:
# Some linux distributions of MKL and MP libraries will run operations multithreaded 
# under the hood. os.environ sets linux environmental variables that control this 
# behavior. Here we're limiting these libraries to using at most 2 threads (vs default ncpu)
# This way we can more predictably control system usage with python multiprocessing

# If you notice weird use of many mores than expected consider setting some of these environmental 
# variable. We can also consider setting them on a system wide level.
os.environ['MKL_NUM_THREADS'] = '1'
os.environ['GOTO_NUM_THREADS'] = '1'
os.environ['OMP_NUM_THREADS'] = '1'

This notebook assumes that you have a dataset with:
    1. Already deconvolved images
    2. Already found beads (will include a section about bead finding since it is an area for improvement)

In [102]:
# Import custom libraries
from metadata import *
from codestack_creation import *
from registration import *
from wrappers import *



In [10]:
# Load configuration for spot_calling
from seqfish_config import *

# Importing codebook (bunch of config options are setup in seqfish_config.py)
# WARNING - this file needs to vary in an experiment/microscopy specific fashion.
gids, cwords = zip(*cbook_dict.items())
bids, blanks = zip(*blank_dict.items())
genes = gids
cvectors = np.stack(cwords, axis=0)
cvectors.shape
nvectors = normalize(cvectors)

md_pth = '/scratch/hRedux_less_subset'
md = Metadata(md_pth)
posnames = md.posnames


In [11]:
from skimage.external.tifffile import TiffWriter
import subprocess
from shlex import split
from skimage import img_as_uint

def stkshow(images, fname='/home/rfor10/Downloads/tmp-stk.tif'):
    with TiffWriter(fname, bigtiff=False, imagej=True) as t:
        if len(images.shape)>2:
            for i in range(images.shape[2]):
                t.save(images[:,:,i].astype('uint16'))
        else:
            t.save(images.astype('uint16'))
#     java_cmd = ["java", "-Xmx5120m", "-jar", "/Users/robertf/ImageJ/ImageJ.app/Contents/Resources/Java/ij.jar"]
#     image_j_args = ["-ijpath", "/Users/robertf/ImageJ/", fname]
#     subprocess.Popen(java_cmd+image_j_args, shell=False,stdin=None,stdout=None,stderr=None,close_fds=True)

In [106]:
# Find beads in 3D
def find_beads_wrapper(posname, md_pth):
    md = Metadata(md_pth)
    fnames = md.stkread(Channel='DeepBlue', Position=posname, groupby='acq', fnames_only=True)
    beads = {}
    substks = {}
    pop_dict = {}
    for h, fnames in fnames.items():
        h = h.split('_')[0]
        ref_beads, ref_substks = find_beads_3D(fnames, ave_bead, match_threshold=0.75)
        
        beads[h] = ref_beads
        substks[h] = ref_substks
        #pop_dict.update(pop_list)
    reg_ref_hybe = 'hybe1'
    if 'nucstain' in beads:
        beads.pop('nucstain')
    max_dist = 30
    verbose=True
    hybe_names = []
    tforms = {reg_ref_hybe: {'tvec': numpy.array([0, 0])}}
    ref_beads = beads.pop(reg_ref_hybe)
    bead_sets = defaultdict(dict)
    # Find beads in nonreference hybes
    tree = KDTree(ref_beads[:, 0:2]) #Data structure for finding close beads quickly
    for h, current_beads in beads.items():
        hybe_names.append(h)
        if verbose:
            print('Registering:', h)
        # Reject bead candidates that are >max_dist from any bead in reference
        dists, idxes = tree.query(current_beads[:, 0:2])
        shifts = []
        # Store all bead candidates in nonreference with their closest
        # cognate bead in the reference
        for b_i, b in enumerate(current_beads):
#             if tuple(b) in pop_dict:
#                 try:
#                     substks[h].pop(tuple(b))
#                     continue
#                 except:
#                     continue
            if dists[b_i]<max_dist:
                bead_sets[tuple(ref_beads[idxes[b_i]])][h] = b

    # Only keep beads found in all hybes 
    master_beads = {}
    for k, v in bead_sets.items():
        if len(v)==len(hybe_names):
            master_beads[k] = v

    master_substks = defaultdict(dict)
    for k, v in master_beads.items():
        v[reg_ref_hybe] = np.array(k)
        master_substks[reg_ref_hybe][k] = substks[reg_ref_hybe][k]
        for h, coords in v.items():
            s = substks[h][tuple(coords)]
            master_substks[h][tuple(coords)] = s
    beads[reg_ref_hybe] = ref_beads
    return beads, substks, master_beads, master_substks


In [79]:
fnames = md.stkread(Channel='DeepBlue', Position=posnames[1], fnames_only=True, groupby='acq')


In [103]:
ref_beads, ref_substks = find_beads_3D(fnames['hybe2_2'], ave_bead, match_threshold=0.75)

In [ ]:
beads, substks, master_beads, master_substks = find_beads_wrapper(posnames[1], md_pth)

In [113]:
substks

{'hybe1': {(2019,
   1359,
   20): array([[[ 5488.,  5696.,  4112.,  3168.,  4896.,  5584.,  5312.],
          [ 7121.,  9313.,  7057.,  4064.,  5616.,  6993.,  5824.],
          [11250., 10834., 10770.,  5840.,  6673.,  8209.,  6353.],
          [ 8177.,  9553., 10610.,  5872.,  7681.,  8161.,  6048.],
          [ 6353.,  6225.,  5616.,  4336.,  6161.,  6529.,  6032.],
          [ 4976.,  3920.,  2624.,  2896.,  4160.,  6128.,  5888.],
          [ 2880.,  2896.,  2704.,  2480.,  3392.,  5072.,  5024.]],
  
         [[ 5408.,  6401.,  5152.,  5344.,  7153.,  7585.,  5584.],
          [ 8913., 10338., 12450., 10866., 10706.,  9217.,  6032.],
          [ 9329., 15923., 22180., 16035., 12322.,  9841.,  6641.],
          [10578., 14483., 18724., 17203., 10946., 11266.,  6801.],
          [ 7217.,  9281., 11138., 10258.,  9873.,  9169.,  6817.],
          [ 4944.,  4208.,  4768.,  6145.,  7601.,  7073.,  5648.],
          [ 3920.,  3472.,  3504.,  4560.,  5504.,  6064.,  5120.]],
  
       

In [105]:
ref_beads.shape

(144, 3)

In [90]:
%pdb

Automatic pdb calling has been turned ON


In [ ]:
import cv
def find_beads_3D_cv2(fnames_list, bead_template, match_threshold=0.75):
    hybe_names = ['hybe1', 'hybe2', 'hybe3', 'hybe4', 'hybe5', 'hybe6']
    #fnames_dict = {k.split('_')[0]:v for k, v in fnames_dict.items()}
#     fish_md = Metadata(md_path, md_name='Metadata.dsv')
#     pos = fish_md.posnames[1]
#     fish_md.image_table = fish_md.image_table[fish_md.image_table.Position==pos]
    #tforms = {reg_reference: {'tvec': numpy.array([0, 0])}}
    #ref_fnames = fnames_dict.pop(reg_reference)
    ref_stk = numpy.stack([io.imread(i) for i in fnames_list], axis=2).astype('float')
    
    ref_match = match_template(ref_stk, bead_template)
    ref_beads = peak_local_max(ref_match, threshold_abs=match_threshold)
    ref_substks, pop_list = fetch_substacks(ref_stk, ref_beads, w=3)
    
    #del ref_stk
    return ref_stk, ref_match, ref_beads, ref_substks, pop_list

In [87]:
ave_bead.shape

(7, 7, 7)

In [71]:
beads[reg_ref_hybe] = ref_beads

In [72]:
reg_ref_hybe = 'hybe1'
#beads.pop('nucstain')
max_dist = 30
verbose=True
hybe_names = []
tforms = {reg_ref_hybe: {'tvec': numpy.array([0, 0])}}
ref_beads = beads.pop(reg_ref_hybe)
bead_sets = defaultdict(dict)
# Find beads in nonreference hybes
tree = KDTree(ref_beads[:, 0:2]) #Data structure for finding close beads quickly
for h, current_beads in beads.items():
    hybe_names.append(h)
    if verbose:
        print('Registering:', h)
    # Reject bead candidates that are >max_dist from any bead in reference
    dists, idxes = tree.query(current_beads[:, 0:2])
    shifts = []
    # Store all bead candidates in nonreference with their closest
    # cognate bead in the reference
    for b_i, b in enumerate(current_beads):
        if dists[b_i]<max_dist:
            bead_sets[tuple(ref_beads[idxes[b_i]])][h] = b

# Only keep beads found in all hybes 
master_beads = {}
for k, v in bead_sets.items():
    if len(v)==len(hybe_names):
        master_beads[k] = v

master_substks = defaultdict(dict)
for k, v in master_beads.items():
    v[reg_ref_hybe] = np.array(k)
    master_substks[reg_ref_hybe][k] = substks[reg_ref_hybe][k]
    for h, coords in v.items():
        s = substks[h][tuple(coords)]
        master_substks[h][tuple(coords)] = s


Registering: hybe2
Registering: hybe3
Registering: hybe4
Registering: hybe5
Registering: hybe6


KeyError: (970, 420, 1)

In [50]:
master_substks = defaultdict(dict)
for k, v in master_beads.items():
    v[reg_ref_hybe] = np.array(k)
    master_substks[reg_ref_hybe][k] = substks[reg_ref_hybe][k]
    for h, coords in v.items():
        s = substks[h][tuple(coords)]
        master_substks[h][tuple(coords)] = s


KeyError: (970, 420, 1)

In [51]:
k

(970, 420, 1)

In [47]:
substks['hybe1']

{(2019,
  1359,
  20): array([[[ 5488.,  5696.,  4112.,  3168.,  4896.,  5584.,  5312.],
         [ 7121.,  9313.,  7057.,  4064.,  5616.,  6993.,  5824.],
         [11250., 10834., 10770.,  5840.,  6673.,  8209.,  6353.],
         [ 8177.,  9553., 10610.,  5872.,  7681.,  8161.,  6048.],
         [ 6353.,  6225.,  5616.,  4336.,  6161.,  6529.,  6032.],
         [ 4976.,  3920.,  2624.,  2896.,  4160.,  6128.,  5888.],
         [ 2880.,  2896.,  2704.,  2480.,  3392.,  5072.,  5024.]],
 
        [[ 5408.,  6401.,  5152.,  5344.,  7153.,  7585.,  5584.],
         [ 8913., 10338., 12450., 10866., 10706.,  9217.,  6032.],
         [ 9329., 15923., 22180., 16035., 12322.,  9841.,  6641.],
         [10578., 14483., 18724., 17203., 10946., 11266.,  6801.],
         [ 7217.,  9281., 11138., 10258.,  9873.,  9169.,  6817.],
         [ 4944.,  4208.,  4768.,  6145.,  7601.,  7073.,  5648.],
         [ 3920.,  3472.,  3504.,  4560.,  5504.,  6064.,  5120.]],
 
        [[ 5232.,  6801.,  6177., 

In [89]:

bead_pth = '/bigstore/Images2018/Robert/ca_celltypes/hybe_mcf10a_serumTitration_redux_deux_less_dense_cells_2018Jun18_2018Jun21/hdf3/'
tforms_xyy, tforms_zz, master_beadss = load_beads_find_tforms(bead_pth)

In [56]:
from collections import Counter

In [98]:
tforms_xy = defaultdict(list)
tforms_z = defaultdict(list)
tforms_z_raw = defaultdict(list)
# Iterate over all beads found in all hybes and fit gaussians then
# find the shift between the reference and nonreference
for k, hybe_dict in master_beads[p].items():
    #if str(k) in ref_substks:
        #sstk = ref_substks[str(k)]
        #ref_fit = gaussfitter.gaussfit(sstk[:,:,3])
    ref_fit = (k[0], k[1])
        #print(ref_fit)
    for h, dest_bead in hybe_dict.items():
            #if str(tuple(dest_bead)) in destination_substks[h]:
        try:
                #sstk = destination_substks[h][str(tuple(dest_bead))]
                #dest_fit = gaussfitter.gaussfit(sstk[:,:,3])
                #dest_fit = (dest_bead[0]+dest_fit[2]-3, dest_bead[1]+dest_fit[3]-3)
            dest_fit = (dest_bead[0], dest_bead[1])
            tforms_xy[h].append(np.subtract(ref_fit, dest_fit))
            tforms_z[h].append((k[2], np.subtract(k[2], dest_bead[2])))
            tforms_z_raw[h].append((k[2], dest_bead[2]))
        except:
            continue

In [105]:
h = 'hybe6'
dzdict = defaultdict(list)
for z, dz in tforms_z[h]:
    dzdict[z].append(dz)
dzdict = {k:(len(v), np.mean(v)+np.mean(tforms_z[h])) for k,v in dzdict.items()}
dzdict

{12: (6, 3.3855721393034828),
 14: (4, 4.052238805970149),
 16: (8, 4.677238805970149),
 17: (11, 4.915875169606513),
 13: (6, 3.5522388059701493),
 8: (4, 4.302238805970149),
 18: (6, 4.218905472636816),
 11: (4, 3.5522388059701493),
 10: (5, 3.1522388059701494),
 1: (1, 4.552238805970149),
 9: (6, 3.8855721393034823),
 5: (1, 4.552238805970149),
 6: (2, 4.552238805970149),
 7: (1, 5.552238805970149),
 2: (1, 3.5522388059701493),
 3: (1, 4.552238805970149)}

In [118]:
# Check that tforms and pseudo-max-projections result in well aligned images with bead stacks

# 
p = posnames[0]
#print(tforms_z)
bead_stk = pseudo_bead_stacks_byposition(p,md_pth, tforms_xyy, tforms_zz, zstart=14, k=1)

[13, 14, 15]
opening img_BL_site46_5_2_000000015_000000000_DeepBlue_000_015.tif[14, 15, 16]
opening img_BL_site46_5_2_000000016_000000000_DeepBlue_000_016.tif[13, 14, 15]
opening img_BL_site46_5_2_000000015_000000000_DeepBlue_000_015.tif[15, 16, 17]
opening img_BL_site46_5_2_000000017_000000000_DeepBlue_000_017.tif[13, 14, 15]
opening img_BL_site46_5_2_000000015_000000000_DeepBlue_000_015.tif[15, 16, 17]
opening img_BL_site46_5_2_000000017_000000000_DeepBlue_000_017.tif

In [ ]:
tforms_z

In [119]:
stkshow(bead_stk)

In [95]:
db = md.stkread(Position=p, Channel='DeepBlue', groupby='acq')

opening img_BR_site67_7_1_000000028_000000000_DeepBlue_000_028.tif

In [100]:
stkshow(db['hybe5_5'])

In [ ]:
cstk_save_dir = '/scratch/hRedux_less_subset/codestacks/'

if not os.path.exists(cstk_save_dir):
    os.makedirs(cstk_save_dir)

multi_z_wrapper(pos_subset[0])